# Performing Validation at Each Round of Training 

## Setting the node up
It is necessary to previously configure a node:
1. `./scripts/fedbiomed_run node add`
  * Select option 2 (default) to add MNIST to the node
  * Confirm default tags by hitting "y" and ENTER
  * Pick the folder where MNIST is downloaded (this is due torch issue https://github.com/pytorch/vision/issues/3549)
  * Data must have been added (if you get a warning saying that data must be unique is because it's been already added)
  
2. Check that your data has been added by executing `./scripts/fedbiomed_run node list`
3. Run the node using `./scripts/fedbiomed_run node start`. Wait until you get `Starting task manager`. it means you are online.

## 1. Validating Pytorch Model Using Predefined Evalution Metrics at each Round of Federeated Training

Declare a torch training plan MyTrainingPlan class to send for training on the node.

In [1]:
import torch
import torch.nn as nn
from fedbiomed.common.training_plans import TorchTrainingPlan
from fedbiomed.common.data import DataManager
from torchvision import datasets, transforms


# Here we define the model to be used. 
# You can use any class name (here 'Net')
class MyTrainingPlan(TorchTrainingPlan):
    
    # Defines and return model 
    def init_model(self, model_args):
        return self.Net(model_args = model_args)
    
    # Defines and return optimizer
    def init_optimizer(self, optimizer_args):
        return torch.optim.Adam(self.model().parameters(), lr = optimizer_args["lr"])
    
    # Declares and return dependencies
    def init_dependencies(self):
        deps = ["from torchvision import datasets, transforms"]
        return deps
    
    class Net(nn.Module):
        def __init__(self, model_args):
            super().__init__()
            self.conv1 = nn.Conv2d(1, 32, 3, 1)
            self.conv2 = nn.Conv2d(32, 64, 3, 1)
            self.dropout1 = nn.Dropout(0.25)
            self.dropout2 = nn.Dropout(0.5)
            self.fc1 = nn.Linear(9216, 128)
            self.fc2 = nn.Linear(128, 10)

        def forward(self, x):
            x = self.conv1(x)
            x = F.relu(x)
            x = self.conv2(x)
            x = F.relu(x)
            x = F.max_pool2d(x, 2)
            x = self.dropout1(x)
            x = torch.flatten(x, 1)
            x = self.fc1(x)
            x = F.relu(x)
            x = self.dropout2(x)
            x = self.fc2(x)


            output = F.log_softmax(x, dim=1)
            return output

    def training_data(self):
        # Custom torch Dataloader for MNIST data
        transform = transforms.Compose([transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))])
        dataset1 = datasets.MNIST(self.dataset_path, train=True, download=False, transform=transform)
        train_kwargs = { 'shuffle': True}
        return DataManager(dataset=dataset1, **train_kwargs)
    
    def training_step(self, data, target):
        output = self.model().forward(data)
        loss   = torch.nn.functional.nll_loss(output, target)
        return loss


### 3.1 Declare and run the experiment
The model is trained on the **MNIST dataset** for classification. For validation, we will be using the **F1-Score**  as a metric. Validation will be performed on both **local updates and global updates**.

In [2]:
from fedbiomed.researcher.experiment import Experiment
from fedbiomed.researcher.aggregators.fedavg import FedAverage


model_args = {}

training_args = {
    'loader_args': { 'batch_size': 48, }, 
    'optimizer_args': {
        "lr" : 1e-3
    },
    'epochs': 1, 
    'dry_run': False,  
    #'batch_maxnum': 100 # Fast pass for development : only use ( batch_maxnum * batch_size ) samples
}


tags =  ['#MNIST', '#dataset']
rounds = 2

exp = Experiment(tags=tags,
                 model_args=model_args,
                 training_plan_class=MyTrainingPlan,
                 training_args=training_args,
                 round_limit=rounds,
                 aggregator=FedAverage(),
                 node_selection_strategy=None,
                tensorboard=True)

2024-02-26 10:43:43,564 fedbiomed INFO - Starting researcher service...

2024-02-26 10:43:43,565 fedbiomed INFO - Waiting 3s for nodes to connect...

2024-02-26 10:43:44,884 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-26 10:43:44,887 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

2024-02-26 10:43:46,577 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

...

2024-02-26 10:43:46,590 fedbiomed INFO - Node selected for training -> NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca

2024-02-26 10:43:46,599 fedbiomed DEBUG - Model file has been saved: /home/ybouilla/Documents/github/fedbiomed/var/experiments/Experiment_0005/model_8332ea94-cf10-4525-881a-31df67f34882.py

Secure RNG turned off. This is perfectly fine for experimentation as it allows for much faster training performance, but remember to turn it on and retrain one last time before production with ``secure_mode`` turned on.


2024-02-26 10:43:46,616 fedbiomed DEBUG - using native torch optimizer

2024-02-26 10:43:46,617 fedbiomed INFO - Removing tensorboard logs from previous experiment

#### Declaring Validation Arguments 

- **test_ratio:** The ratio for validation partition 
- **test_metric:** The metric that is going to be used for validation
- **Validation on local updates:** Means that validation is going to be perform after training is performed over aggreated paramaters  
- **Validation on global updates**: Means that validation will be perform on aggregated parameters before performing the training. 


You can display all the default metrics that are supported in Fed-BioMed. They are all based on sklearn metrics

In [3]:
from fedbiomed.common.metrics import MetricTypes
MetricTypes.get_all_metrics()

['ACCURACY',
 'F1_SCORE',
 'PRECISION',
 'RECALL',
 'MEAN_SQUARE_ERROR',
 'MEAN_ABSOLUTE_ERROR',
 'EXPLAINED_VARIANCE']

In [4]:
exp.set_test_ratio(0.1)
exp.set_test_on_local_updates(True)
exp.set_test_on_global_updates(True)
exp.set_test_metric(MetricTypes.F1_SCORE)

2024-02-26 10:43:46,644 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-26 10:43:46,646 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-26 10:43:46,647 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-26 10:43:46,649 fedbiomed DEBUG - Experimentation training_args updated for `job`

(<MetricTypes.F1_SCORE: (1, <_MetricCategory.CLASSIFICATION_LABELS: 0>)>, {})

Launch tensorboard

In [5]:
from fedbiomed.researcher.environ import environ
tensorboard_dir = environ['TENSORBOARD_RESULTS_DIR']

In [6]:
%load_ext tensorboard

In [7]:
%tensorboard --logdir "$tensorboard_dir"

Let's start the experiment.

By default, this function doesn't stop until all the `round_limit` rounds are done for all the nodes

In [8]:
exp.run()

2024-02-26 10:43:47,690 fedbiomed INFO - Sampled nodes in round 0 ['NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf', 'NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca']

2024-02-26 10:43:47,693 fedbiomed INFO - Sending request 
					 To: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 10:43:47,694 fedbiomed INFO - Sending request 
					 To: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 10:43:47,739 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

2024-02-26 10:43:47,744 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

...

2024-02-26 11:15:02,360 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Round 3 | Iteration: 120/125 (96%) | Samples: 5760/6000
 					 F1_SCORE: 1.000000 
					 ---------

2024-02-26 11:15:02,926 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Round 3 | Iteration: 125/125 (100%) | Samples: 6000/6000
 					 F1_SCORE: 0.979167 
					 ---------

2024-02-26 11:15:02,940 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 3 | Iteration: 120/125 (96%) | Samples: 5760/6000
 					 F1_SCORE: 1.000000 
					 ---------

2024-02-26 11:15:02,995 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 3 | Iteration: 125/125 (100%) | Samples: 6000/6000
 					 F1_SCORE: 1.000000 
					 ---------

2



## 2. Training and Validation with sklearn Perceptron model


Now we will use the validation facility on Skelearn training plan

In [9]:
from fedbiomed.common.training_plans import FedPerceptron


class SkLearnClassifierTrainingPlan(FedPerceptron):
    def init_dependencies(self):
        return ["from torchvision import datasets, transforms",]

    def training_data(self):
        # Custom torch Dataloader for MNIST data: np.ndarray
        transform = transforms.Compose([transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))])
        dataset = datasets.MNIST(self.dataset_path, train=True, download=False, transform=transform)
        
        X_train = dataset.data.numpy()
        X_train = X_train.reshape(-1, 28*28)
        Y_train = dataset.targets.numpy()
        
        return DataManager(dataset=X_train,target=Y_train,  shuffle=True)

It is also possible to define validation option in the training arguments. 

In [10]:
model_args = { 'max_iter':1000,
              'tol': 1e-4 ,
              'model': 'Perceptron' ,
              'n_features': 28*28,
              'n_classes' : 10,
              'eta0':1e-6,
              'random_state':1234,
              'alpha':0.1 }

training_args = {
    'epochs': 5, 
    'loader_args': { 'batch_size': 48, }
}

In [11]:
from fedbiomed.researcher.experiment import Experiment
from fedbiomed.researcher.aggregators.fedavg import FedAverage

tags =  ['#MNIST', '#dataset']
rounds = 10

# select nodes participing to this experiment
exp = Experiment(tags=tags,
                 model_args=model_args,
                 training_plan_class=SkLearnClassifierTrainingPlan,
                 training_args=training_args,
                 round_limit=rounds,
                 aggregator=FedAverage(),
                 node_selection_strategy=None, 
                 tensorboard=True)


exp.set_test_ratio(.2)
#exp.set_test_metric(MetricTypes.PRECISION, average='macro')
exp.set_test_on_global_updates(True)

2024-02-26 11:16:46,290 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-26 11:16:46,291 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

2024-02-26 11:16:46,293 fedbiomed INFO - Node selected for training -> NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf

2024-02-26 11:16:46,293 fedbiomed INFO - Node selected for training -> NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca

2024-02-26 11:16:46,295 fedbiomed DEBUG - Model file has been saved: /home/ybouilla/Documents/github/fedbiomed/var/experiments/Experiment_0006/model_7d35a103-9b0a-4d3b-945a-6d71da3ab30a.py

2024-02-26 11:16:46,296 fedbiomed DEBUG - Using native Sklearn Optimizer

2024-02-26 11:16:46,298 fedbiomed INFO - Removing tensorboard logs from previous experiment

2024-02-26 11:16:46,300 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-26 11:16:46,301 fedbiomed DEBUG - Experimentation training_args updated for `job`

True

In [12]:
exp.run_once(increase=True)

2024-02-26 11:16:48,964 fedbiomed INFO - Sampled nodes in round 0 ['NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf', 'NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca']

2024-02-26 11:16:48,966 fedbiomed INFO - Sending request 
					 To: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 11:16:48,967 fedbiomed INFO - Sending request 
					 To: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 11:16:48,970 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-26 11:16:48,971 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

...

2024-02-26 11:26:16,788 fedbiomed INFO - TRAINING 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 1 Epoch: 5 | Iteration: 990/1000 (99%) | Samples: 47520/48000
 					 Loss perceptron: 27653.693359 
					 ---------

2024-02-26 11:26:17,839 fedbiomed INFO - TRAINING 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 1 Epoch: 5 | Iteration: 1000/1000 (100%) | Samples: 48000/48000
 					 Loss perceptron: 22876.746094 
					 ---------

2024-02-26 11:26:17,851 fedbiomed INFO - Nodes that successfully reply in round 0 ['NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf', 'NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca']

2024-02-26 11:26:17,853 fedbiomed INFO - Saved aggregated params for round 0 in /home/ybouilla/Documents/github/fedbiomed/var/experiments/Experiment_0006/aggregated_params_63ff9685-4de1-4b1b-8460-ea2fe529686d.mpk

1

Feel free to run other sample notebooks or try your own models :D

# 3. Validation facility using your own testing metric

If the user wants to define its own testing metric, he can do so by defining the `testing_step` method in the Training plan. 

`testing_step` is defined the same way as `training_step`:

When defining a `testing_step` method in the TrainingPlan, user has to:
- predict classes or probabilities from model
- compute a scalar or a list of scalars

Method `testing_step` can return either a scalar or a list of scalars: in Tensorboard, list of scalars will be seen as the output of several metrics


## 3.1 PyTorch Training Plan

Below we showcase an example of a TorchTrainingPlan with a `testing_step` computing 3 metrics: log likelihood loss, a cross entropy loss, and a custom accuracy metric 

In [13]:
import torch
import torch.nn as nn
from fedbiomed.common.training_plans import TorchTrainingPlan
from fedbiomed.common.data import DataManager
from torchvision import datasets, transforms

# Here we define the model to be used. 
# You can use any class name (here 'Net')
class MyTrainingPlanCM(TorchTrainingPlan):
    
    # Defines and return model 
    def init_model(self, model_args):
        return self.Net(model_args = model_args)
    
    # Defines and return optimizer
    def init_optimizer(self, optimizer_args):
        return torch.optim.Adam(self.model().parameters(), lr = optimizer_args["lr"])
    
    # Declares and return dependencies
    def init_dependencies(self):
        deps = ["from torchvision import datasets, transforms"]
        return deps
    
    class Net(nn.Module):
        def __init__(self, model_args):
            super().__init__()
            self.conv1 = nn.Conv2d(1, 32, 3, 1)
            self.conv2 = nn.Conv2d(32, 64, 3, 1)
            self.dropout1 = nn.Dropout(0.25)
            self.dropout2 = nn.Dropout(0.5)
            self.fc1 = nn.Linear(9216, 128)
            self.fc2 = nn.Linear(128, 10)

        def forward(self, x):
            x = self.conv1(x)
            x = F.relu(x)
            x = self.conv2(x)
            x = F.relu(x)
            x = F.max_pool2d(x, 2)
            x = self.dropout1(x)
            x = torch.flatten(x, 1)
            x = self.fc1(x)
            x = F.relu(x)
            x = self.dropout2(x)
            x = self.fc2(x)


            output = F.log_softmax(x, dim=1)
            return output

    def training_data(self):
        # Custom torch Dataloader for MNIST data
        transform = transforms.Compose([transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))])
        dataset1 = datasets.MNIST(self.dataset_path, train=True, download=False, transform=transform)
        train_kwargs = { 'shuffle': True}
        return DataManager(dataset=dataset1, **train_kwargs)
    
    def training_step(self, data, target):
        output = self.model().forward(data)
        loss   = torch.nn.functional.nll_loss(output, target)
        return loss

    def testing_step(self, data, target):
        output = self.model().forward(data)

        #negative log likelihood loss
        loss1 = torch.nn.functional.nll_loss(output, target)

        #cross entropy
        loss2 = torch.nn.functional.cross_entropy(output,target)

        # accuracy
        _,predicted = torch.max(output.data,1)
        acc = torch.sum(predicted==target)
        loss3 = acc/len(target)

        # Returning results as list
        return [loss1,loss2,loss3]

In [14]:
model_args = {}

training_args = {
    'loader_args': { 'batch_size': 48, }, 
    'optimizer_args': {
        'lr': 1e-3,   
    },
    'epochs': 1, 
    'dry_run': False,  
    'batch_maxnum': 100, # Fast pass for development : only use ( batch_maxnum * batch_size ) samples
    'test_ratio': .3,
    'test_on_local_updates': True, 
    'test_on_global_updates': True
}

In [15]:
from fedbiomed.researcher.experiment import Experiment
from fedbiomed.researcher.aggregators.fedavg import FedAverage

tags =  ['#MNIST', '#dataset']
rounds = 2

exp = Experiment(tags=tags,
                 model_args=model_args,
                 training_plan_class=MyTrainingPlanCM,
                 training_args=training_args,
                 round_limit=rounds,
                 aggregator=FedAverage(),
                 node_selection_strategy=None, 
                 tensorboard=True)

2024-02-26 11:27:22,009 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

2024-02-26 11:27:22,011 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-26 11:27:22,013 fedbiomed INFO - Node selected for training -> NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf

2024-02-26 11:27:22,014 fedbiomed INFO - Node selected for training -> NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca

2024-02-26 11:27:22,016 fedbiomed DEBUG - Model file has been saved: /home/ybouilla/Documents/github/fedbiomed/var/experiments/Experiment_0007/model_344679aa-4508-4844-9e57-f97f8b9cccbe.py

Secure RNG turned off. This is perfectly fine for experimentation as it allows for much faster training performance, but remember to turn it on and retrain one last time before production with ``secure_mode`` turned on.


2024-02-26 11:27:22,024 fedbiomed DEBUG - using native torch optimizer

2024-02-26 11:27:22,025 fedbiomed INFO - Removing tensorboard logs from previous experiment

In [16]:
exp.run()

2024-02-26 11:27:22,149 fedbiomed INFO - Sampled nodes in round 0 ['NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf', 'NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca']

2024-02-26 11:27:22,154 fedbiomed INFO - Sending request 
					 To: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 11:27:22,156 fedbiomed INFO - Sending request 
					 To: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-26 11:27:22,219 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-26 11:27:22,224 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

...

2024-02-26 11:40:48,968 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 3 | Iteration: 360/375 (96%) | Samples: 17280/18000
 					 Custom_2: 0.296252 
					 Custom_1: 0.296252 
					 Custom_3: 0.958333 
					 ---------

2024-02-26 11:40:49,141 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 3 | Iteration: 370/375 (99%) | Samples: 17760/18000
 					 Custom_2: 0.113911 
					 Custom_1: 0.113911 
					 Custom_3: 0.958333 
					 ---------

2024-02-26 11:40:49,225 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 3 | Iteration: 375/375 (100%) | Samples: 18000/18000
 					 Custom_2: 0.125657 
					 Custom_1: 0.125657 
					 Custom_3: 0.979167 
					 ---------

2

2024-02-26 11:41:30,571 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

## 3.2 Sklearn Training Plan

Below we showcase an example of a SklearnTrainingPlan with a `testing_step` computing several metrics

In [1]:
from fedbiomed.common.training_plans import FedPerceptron
from fedbiomed.common.data import DataManager

import numpy as np
from sklearn.metrics import hinge_loss


class SkLearnClassifierTrainingPlan(FedPerceptron):
    mnist_label = np.arange(10) # specify all classes for MNIST dataset
    def init_dependencies(self):
        return ["from torchvision import datasets, transforms",
                "from torch.utils.data import DataLoader",
                "from sklearn.metrics import hinge_loss"]

    def compute_true_positive(self, data, target):
        tp: float = 0.
        for digit in self.mnist_label:
            idx_data_equal_to_digit = (target.squeeze() == digit)
            if np.all(np.logical_not(idx_data_equal_to_digit)):
                continue  # no digit found in the targets of this batch
            predicted = self.model().predict(data[idx_data_equal_to_digit])
        
            tp += np.sum(predicted==digit)
        tp /= len(target)
        
        return tp

    def training_data(self):
        # Custom torch Dataloader for MNIST data
        transform = transforms.Compose([transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))])
        dataset = datasets.MNIST(self.dataset_path, train=True, download=False, transform=transform)
        
        train_kwargs = { 'shuffle': True}  # number of data passed to classifier
        X_train = dataset.data.numpy()
        X_train = X_train.reshape(-1, 28*28)
        Y_train = dataset.targets.numpy()
        
        return DataManager(dataset=X_train, target=Y_train)
    
    def testing_step(self, data, target):
        # hinge loss

        distance_from_hyperplan = self.model().decision_function(data)
        
        loss = hinge_loss(target, distance_from_hyperplan, labels=self.mnist_label)
        
        # get the true positive rate for all the digit of MNIST 
        tp = self.compute_true_positive(data, target)
        # Returning results as dict
        return {'Hinge Loss': loss, 'true positive': tp }

In [2]:
model_args = { 'max_iter':1000,
              'tol': 1e-4 ,
              'model': 'Perceptron' ,
              'n_features': 28*28,
              'n_classes' : 10,
              'eta0':1e-6,
              'random_state':1234,
              'alpha':0.1 }

training_args = {
    'epochs': 5,
    'loader_args': { 'batch_size': 48, }, 
}


In [3]:
from fedbiomed.researcher.experiment import Experiment
from fedbiomed.researcher.aggregators.fedavg import FedAverage

tags =  ['#MNIST', '#dataset']
rounds = 10

# select nodes participing to this experiment
exp = Experiment(tags=tags,
                 model_args=model_args,
                 training_plan_class=SkLearnClassifierTrainingPlan,
                 training_args=training_args,
                 round_limit=rounds,
                 aggregator=FedAverage(),
                 node_selection_strategy=None, 
                 tensorboard=True)


exp.set_test_ratio(.2)
#exp.set_test_metric(MetricTypes.PRECISION, average='macro')
exp.set_test_on_global_updates(True)
exp.set_test_on_local_updates(True)

2024-02-27 13:11:21,425 fedbiomed INFO - Starting researcher service...

2024-02-27 13:11:21,460 fedbiomed INFO - Waiting 3s for nodes to connect...

2024-02-27 13:11:22,293 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

2024-02-27 13:11:22,295 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-27 13:11:24,477 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

...

2024-02-27 13:11:24,491 fedbiomed DEBUG - Using native Sklearn Optimizer

2024-02-27 13:11:24,492 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-27 13:11:24,493 fedbiomed DEBUG - Experimentation training_args updated for `job`

2024-02-27 13:11:24,494 fedbiomed DEBUG - Experimentation training_args updated for `job`

True

In [4]:
exp.run(increase=True)

2024-02-27 13:11:24,500 fedbiomed INFO - Sampled nodes in round 0 ['NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca', 'NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf']

2024-02-27 13:11:24,501 fedbiomed INFO - Sending request 
					 To: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-27 13:11:24,501 fedbiomed INFO - Sending request 
					 To: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf 
					 Request: : TRAIN
 -----------------------------------------------------------------

2024-02-27 13:11:24,506 fedbiomed DEBUG - Node: NODE_8b9c2b34-0d9e-4e9d-a560-b48865746abf polling for the tasks

2024-02-27 13:11:24,506 fedbiomed DEBUG - Node: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca polling for the tasks

...

2024-02-27 14:36:59,842 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 11 | Iteration: 220/250 (88%) | Samples: 10560/12000
 					 Hinge Loss: 5984.904297 
					 true positive: 0.854167 
					 ---------

2024-02-27 14:36:59,871 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 11 | Iteration: 230/250 (92%) | Samples: 11040/12000
 					 Hinge Loss: 1164.546387 
					 true positive: 0.979167 
					 ---------

2024-02-27 14:36:59,892 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 11 | Iteration: 240/250 (96%) | Samples: 11520/12000
 					 Hinge Loss: 2818.987305 
					 true positive: 0.875000 
					 ---------

2024-02-27 14:36:59,903 fedbiomed INFO - VALIDATION ON GLOBAL UPDATES 
					 NODE_ID: NODE_ecaa06d4-2df6-4b76-97f9-39df74f313ca 
					 Round 11 | Iteration: 250/250 (100%) | Samples: 12000/12000
 					 Hinge Loss: 513.839844 
					 true positive: 0.958333 
					 ---------

10